In [1]:
%%capture

import warnings

warnings.filterwarnings("ignore")
import calitp_data_analysis.magics

import geopandas as gpd
import pandas as pd

from great_tables import GT

import _report_utils
from update_vars import GTFS_DATA_DICT, RT_SCHED_GCS

SHARED_GCS = GTFS_DATA_DICT.gcs_paths.SHARED_GCS

In [2]:
import google.auth

credentials, project = google.auth.default()

import gcsfs

fs = gcsfs.GCSFileSystem()

In [3]:
# Comment out and leave this cell right below pandas
# district = "AD 03"

In [4]:
# Parameters
district = "SD 05"


In [5]:
legislative_crosswalk = pd.read_parquet(
    f"{SHARED_GCS}crosswalk_transit_operators_legislative_districts.parquet",
    filters = [[("legislative_district", "==", district)]]
)

def readable_district_name(word: str) -> str:
    if "SD" in word:
        return word.replace("SD", "Senate District")
    elif "AD" in word:
        return word.replace("AD", "Assembly District")

district_full_name = readable_district_name(district)

In [6]:
%%capture_parameters
district, district_full_name

In [7]:
# Read in all datasets here with GTFS_DATA_DICT 
# Reran merge_operator_data.py to test this
OPERATOR_FILE = GTFS_DATA_DICT.digest_tables.operator_profiles
OPERATOR_ROUTE = GTFS_DATA_DICT.digest_tables.operator_routes_map
operator_df = pd.read_parquet(
    f"{RT_SCHED_GCS}{OPERATOR_FILE}.parquet",
).merge(
    legislative_crosswalk,
    on = "name",
    how = "inner"
)

# using name instead of schedule_gtfs_dataset_key allows us to get 
# the last ones for LA Metro without keeping extraneous rows for LA Metro when keys changed
operator_df = operator_df.sort_values(
    ["service_date", "name"], 
    ascending=[False, True]
).drop_duplicates(
    subset=["name"]
).reset_index(drop=True)

# SD 05

These are district summaries for [GTFS Digest](https://gtfs-digest--cal-itp-data-analyses.netlify.app/). 

In [8]:
district_summary = _report_utils.district_stats(
    operator_df, 
    "legislative_district"
)

In [9]:
summary_table1 = (GT(
    district_summary.drop(
        columns = ["arrivals_per_stop", "trips_per_operator"]
    ).pipe(
        _report_utils.transpose_summary_stats, 
        district_col = "legislative_district"
    )
)
 .fmt_integer(columns="value")
 .cols_label(index="")
 .tab_header(title = f"{district_full_name} GTFS summary stats")
)

summary_table2 = (GT(
    district_summary[
        ["legislative_district", "arrivals_per_stop", "trips_per_operator"]
    ].pipe(
        _report_utils.transpose_summary_stats,
        district_col = "legislative_district"
    )
)
 .fmt_number("value", decimals=1)
 .cols_label(index="")
)

In [10]:
display(summary_table1)
display(summary_table2)

GT(_tbl_data=         index    Value
0  # Operators       15
1     # routes      513
2      # trips   11,647
3      # stops    9,460
4   # arrivals  347,521, _body=<great_tables._gt_data.Body object at 0x7898b9e7c190>, _boxhead=Boxhead([ColInfo(var='index', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='left', column_width=None), ColInfo(var='Value', type=<ColInfoTypeEnum.default: 1>, column_label='Value', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7898c83fc690>, _spanners=Spanners([]), _heading=Heading(title='Senate District 05 GTFS summary stats', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7898b9e4a010>, _formats=[<great_tables._gt_data.FormatInfo object at 0x789871369d10>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_left_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_left_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), heading_background_color=OptionsInfo(scss=True, category='heading', type='value', value=None), heading_align=OptionsInfo(scss=True, category='heading', type='value', value='center'), heading_title_font_size=OptionsInfo(scss=True, category='heading', type='px', value='125%'), heading_title_font_weight=OptionsInfo(scss=True, category='heading', type='value', value='initial'), heading_subtitle_font_size=OptionsI

GT(_tbl_data=                index   Value
0   Arrivals per Stop   36.74
1  Trips per Operator  776.47, _body=<great_tables._gt_data.Body object at 0x78987136b010>, _boxhead=Boxhead([ColInfo(var='index', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='left', column_width=None), ColInfo(var='Value', type=<ColInfoTypeEnum.default: 1>, column_label='Value', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x78987133cc10>, _spanners=Spanners([]), _heading=Heading(title=None, subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x789871342cd0>, _formats=[<great_tables._gt_data.FormatInfo object at 0x789871341a50>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_left_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_left_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), heading_background_color=OptionsInfo(scss=True, category='heading', type='value', value=None), heading_align=OptionsInfo(scss=True, category='heading', type='value', value='center'), heading_title_font_size=OptionsInfo(scss=True, category='heading', type='px', value='125%'), heading_title_font_weight=OptionsInfo(scss=True, category='heading', type='value', value='initial'), heading_subtitle_font_size=OptionsInfo(scss=True, category='heading', type='px', value='85%'), heading_subtitle_font_weight=

## GTFS Stats by Operator

In [11]:
operators_in_district = operator_df.schedule_gtfs_dataset_key.unique()

In [12]:
operator_route_gdf = gpd.read_parquet(
    f"{RT_SCHED_GCS}{OPERATOR_ROUTE}.parquet",
    storage_options={"token": credentials.token},
)

In [13]:
operator_route_gdf = operator_route_gdf.loc[
    operator_route_gdf.schedule_gtfs_dataset_key.isin(operators_in_district)
][["name", "service_date", "recent_combined_name", "geometry"]]

In [14]:
operator_route_gdf = operator_route_gdf.sort_values(
    ["service_date", "name", "recent_combined_name"], 
    ascending=[False, True, True]
).drop_duplicates(
    subset = ["name", "recent_combined_name"]
).drop(
    columns = ["service_date", "recent_combined_name"]
    # drop route because after the dissolve, all operator routes are combined
    # so route would hold only the first row's value
).dissolve(by = "name").reset_index().pipe(_report_utils.replace_column_names)


In [15]:
operator_route_gdf["Transit Operator"] = operator_route_gdf["Transit Operator"].str.replace(" Schedule", "")

In [16]:
try:
    operator_route_gdf.explore(
    "Transit Operator", 
    tiles = "CartoDB Positron",
    categorical=True,
    legend=True,
    legend_kwds = {
        "width": 200
    })
except:
    pass

In [17]:
shared_cols = ["organization_name", "name"]
exclude_cols = ["schedule_gtfs_dataset_key", "legislative_district",
                "organization_source_record_id", "service_date", 
                "primary_uza"]

gtfs_service_cols = [
    c for c in operator_df.columns 
    if "operator_" in c]

In [18]:
gtfs_table_df = operator_df[
    shared_cols + gtfs_service_cols
].pipe(_report_utils.replace_column_names)

In [19]:
string_cols = gtfs_table_df.select_dtypes(include="object").columns.tolist()

gtfs_table = (
    GT(gtfs_table_df.sort_values("# Trips", ascending=False))
    .fmt_integer(
        columns = [
            c for c in gtfs_table_df.columns if c not in 
         ["Operator Service Miles", "Avg Arrivals per Stop"]
            and (c not in string_cols)
        ])
    .fmt_number(
        columns = ["Operator Service Miles", "Avg Arrivals per Stop"], 
        decimals = 1)
    .data_color(
        columns=["# Trips", "Avg Arrivals per Stop"],
        palette=["white", "green"],
        na_color="lightgray")
    .tab_header(
         title = f"{district_full_name}",
         subtitle = "Daily GTFS schedule statistics by operator")
    .cols_align(columns = [c for c in gtfs_table_df.columns if c not in ["Organization", "Transit Operator"]],
        align="center")
    )

gtfs_table = _report_utils.great_table_formatting(gtfs_table)
gtfs_table

GT(_tbl_data=                                     Organization  \
1           Alameda-Contra Costa Transit District   
8           San Joaquin Regional Transit District   
9           Stanislaus Regional Transit Authority   
3   San Francisco Bay Area Rapid Transit District   
4          Central Contra Costa Transit Authority   
6                                       Greyhound   
0                                          Amtrak   
5       Livermore-Amador Valley Transit Authority   
12                                  City of Tracy   
13                                City of Manteca   
7                                    City of Lodi   
11                              Sacramento County   
2            San Joaquin Regional Rail Commission   
10                                City of Escalon   
14                                  City of Ripon   

                           Transit Operator  # Routes  # Trips  # Shapes  \
1          Bay Area 511 AC Transit Schedule        84     5320       201   
8                      San Joaquin Schedule        35     1253        87   
9                          StanRTA Schedule        27     1043        55   
3                Bay Area 511 BART Schedule        12     1025        26   
4   Bay Area 511 County Connection Schedule        26      878        60   
6                          Flixbus Schedule       222      871       759   
0                           Amtrak Schedule        59      587       131   
5   Bay Area 511 Tri-Valley Wheels Schedule        18      412        48   
12                           Tracy Schedule        14       76        16   
13                         Manteca Schedule         5       75         7   
7                        Grapeline Schedule         5       65         5   
11       South County Transit Link Schedule         3       24         7   
2                 Bay Area 511 ACE Schedule         1        8         2   
10                          eTrans Schedule         1        6         2   
14                 Blossom Express Schedule         1        4         1   

    # Stops  # Arrivals  Operator Service Miles  Avg Arrivals per Stop  
1      4179      228741                 1053.05                  54.74  
8       869       21372                  474.18                  24.59  
9       911       31261                  453.56                  34.32  
3       105       14845                  490.34                 141.38  
4       943       23154                  304.34                  24.55  
6       888        5665                92107.85                   6.38  
0       509        4117                35028.54                   8.09  
5       464       11294                  238.22                  24.34  
12      234        2536                  203.85                  10.84  
13       83        1385                   51.27                  16.69  
7       178        2678                   56.13                  15.04  
11       22         148                  170.43                   6.73  
2        10          80                   85.85                   8.00  
10       42         153                   13.39                   3.64  
14       23          92                   18.90                   4.00  , _body=<great_tables._gt_data.Body object at 0x789845e81e50>, _boxhead=Boxhead([ColInfo(var='Organization', type=<ColInfoTypeEnum.default: 1>, column_label='Organization', column_align='left', column_width=None), ColInfo(var='Transit Operator', type=<ColInfoTypeEnum.default: 1>, column_label='Transit Operator', column_align='left', column_width=None), ColInfo(var='# Routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='# Trips', type=<ColInfoTypeEnum.default: 1>, column_label='# Trips', column_align='center', column_width=None), ColInfo(var='# Shapes', type=<ColInfoTypeEnum.default: 1>, column_label='# Shapes', column_align='center', column_width=None), ColInfo(var='# Stops